# 环境设置
1. 输出电压设置58V
2. 输入源设置光伏模式, Vmppt=42V, Power=650W
3. 初始化设备;

In [1]:
import time
from pathlib import Path
from device.LaminaAdapter import LaminaAdapter
from device.LaminaAdapter import GeneratePackage_SLCP001_p4a0, GeneratePackage_SLCP101_p460, GeneratePackage_DLSY001_p460
from device.LaminaAdapter import GeneratePackage_SLCP102_p460
from device.tools.ByteConv import trans_list_to_str, trans_str_to_list

In [3]:
mode_config = {
    "Log": {'com_name': None, 
            # 'addr_645': [0x01, 0x00, 0x00, 0x00, 0x00, 0x40], 
            },
    "Debug": {'com_name': 'COM3', 'baudrate': 115200, 'parity': 'N', 'bytesize': 8, 'stopbits': 1,
            #   'addr_645': [0x01, 0x02, 0x03, 0x04, 0x05, 0x06], 
                'frame_print': True, 
                'time_out': 0.5, 'retry': 1, 'retry_sub': 10},
    "HPLC":  {'com_name': 'COM9', 'baudrate': 9600, 'parity': 'E', 'bytesize': 8, 'stopbits': 1,
                'addr_645': trans_str_to_list("02 01 00 00 24 20"), 
                'frame_print': True, 
                'time_out': 3, 'time_gap': 0.1, 'retry': 3, 'retry_sub': 10},
}

dev_lamina = LaminaAdapter(type_dev="SLCP101", **mode_config['Debug'])

In [3]:
def test_communication(time_out=2):
    """ 通信成功率测试 """
    time_start = time.time()
    param_saved = dev_lamina.flag_print, dev_lamina.retry, dev_lamina.time_out
    dev_lamina.flag_print = False
    dev_lamina.retry = 1
    try:
        while True:
            dev_lamina.frame_read(0x0C, 0x20)
            print(f"Time Stamp: {time.ctime()}")
            print(f"Success Frame: {dev_lamina.log['read']}")
            print(f"Failed  Frame: {dev_lamina.log['send'] - dev_lamina.log['read']}")
            print(f"Max Series Failed Frame: {dev_lamina.log['keep-fail']}")
            time.sleep(time_out)
    finally:
        time_end = time.time()
        print("Test Result: ")
        print(f"Time Start: {time.strftime(r'%Y-%m-%d %H:%M:%S', time.localtime(time_start))}, \tTime End: {time.strftime(r'%Y-%m-%d %H:%M:%S', time.localtime(time_end))}")
        print(f"Time Elapsed: {time_end - time_start}")
        print(f"Success Rate: {dev_lamina.log['read'] / dev_lamina.log['send'] * 100}%")
        dev_lamina.flag_print, dev_lamina.retry, dev_lamina.time_out = param_saved

In [5]:
dev_lamina.frame_read(0x0100, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 01 00 00 20 45 EE 4B 16
Read Frame:  68 01 02 03 04 05 06 68 9F 45 01 03 40 48 46 45 43 30 30 5F 31 34 32 31 31 37 30 31 5F 30 37 5F 30 33 56 30 2E 00 31 00 00 00 00 00 00 48 46 45 43 30 30 00 31 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 00 BF A8 EE 16
Parse Result:
0x0100: FHCE001_241107_1700_V3.01        版本(ODM)
0x0110: FHCE001                          型号     


True

# 设备升级

## 单次升级

In [7]:
# 工程-即时转换
if dev_lamina.device == 'SLCP001':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V1\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'SLCP101':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V2.03\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'SLCP102':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V3.01\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'DLSY001':
    file_hex = Path(r"D:\WorkingProject\LightStackOptimizer\software\lamina_optimizer\lamina_optimizer\Debug\lamina_optimizer.hex")
else:
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\lamina_adapter\Debug\lamina_adapter.hex")
if not file_hex.exists():
    raise Exception("工程编译目标文件不存在.")

dev_lamina.frame_update(file_hex, makefile=True)


Package generated successfully.
File name: lamina_adapter.hex
File Info:
	 header_length=184, bin_length=127750[0x1f306]


File Transmitting: 100%|██████████| 592/592 [00:27<00:00, 21.20it/s]


True

## 连续升级

In [ ]:
# 工程-即时转换
if dev_lamina.device == 'SLCP001':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V1\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'SLCP101':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V2.03\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'SLCP102':
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\release\device_V3.01\lamina_adapter\Debug\lamina_adapter.hex")
elif dev_lamina.device == 'DLSY001':
    file_hex = Path(r"D:\WorkingProject\LightStackOptimizer\software\lamina_optimizer\lamina_optimizer\Debug\lamina_optimizer.hex")
else:
    file_hex = Path(r"D:\WorkingProject\LightStackAdapter\software\lamina_adapter\lamina_adapter\Debug\lamina_adapter.hex")
if not file_hex.exists():
    raise Exception("工程编译目标文件不存在.")
print(dev_lamina.device)
print(file_hex)

# 设置升级配置
version = "SLCP101_241030_2000_V2.03"
addr = [0x24, 0x09, 0x12, 0x00, 0x00, 0x00]
dev_lamina.flag_print = False

In [ ]:
while True:
    """ 自动检测升级流程 """
    ret = False
    while not (ret and ('Regs' in dev_lamina.output.keys()) and 
               (version == dev_lamina.output['Regs'][0x0100][1].strip('\000'))):
        # dev_lamina.frame_read(0x82, 3)
        ret = dev_lamina.frame_read(0x0100, 0x20)
        time.sleep(1)

    dev_lamina.frame_update(file_hex, makefile=True)

    time.sleep(3)

    ret = dev_lamina.frame_read(0x0100, 0x20)

    if ret and (version == dev_lamina.output['Regs'][0x0100][1]):
        dev_lamina.frame_write_one(0x52, 0x01)

# 参数还原

In [166]:
dev_lamina.frame_write_one(0x52, 0x01)
time.sleep(4.5)
dev_lamina.frame_write_one(0x53, 0x01)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 52 00 01 E9 DB 11 16
Read Frame:  68 16 95 11 16 06 24 68 9F 08 01 06 00 52 00 01 E9 DB 91 16
Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 53 00 01 B8 1B 21 16
Read Frame:  68 16 95 11 16 06 24 68 9F 08 01 06 00 53 00 01 B8 1B A1 16


True

# 读取设备状态

In [7]:
dev_lamina.frame_read(0x60, 0x60)
time.sleep(0.5)
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 60 00 60 45 FC F8 16
Read Frame:  68 01 02 03 04 05 06 68 9F C5 01 03 C0 00 00 00 79 02 62 00 5A 02 6C 00 64 02 1C 01 CC 02 3A 01 A4 02 44 02 94 02 58 01 B8 09 60 07 D0 00 0A 08 98 02 3A 02 35 02 21 04 1A 03 B6 03 52 01 5E 02 30 AE 60 00 0A 03 E8 00 00 EB 10 00 09 EB 10 00 09 05 06 03 04 01 02 09 C4 FE 0C 00 64 00 00 00 64 00 0D 03 96 00 96 C3 50 00 00 00 C8 00 00 00 FA 00 00 00 14 00 00 00 02 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 03 E8 00 00 00 00 00 00 00 00 03 E8 37 E2 2D BE 02 23 00 00 0C AD 03 FF FF FF FF FF FF FF FF FF FF FF 4C 53 50 43 30 31 5F 32 34 32 31 31 37 30 31 5F 30 37 5F 30 33 56 30 2E 00 31 00 00 00 00 00 00 99 46 20 16
Parse Result:
0x0060: 0x0000                           光伏通道使能               
0x0061: 12.1                             最小启动输入电压             
0x0062: 61.0                             最大启动输入电压             
0x0063: 9.0                              最小停止输入电压             
0x0064: 62.0         

True

In [164]:
test_communication()

Parse Result:
0x000C: 0xFFFF 未知数据     
0x000D: 0xFFFF 未知数据     
0x000E: 0x0000 故障字1     
0x000F: 0x0000 故障字2     
0x0010: 0x0000 MPPT工作状态 
0x0011: 0x0000 系统工作状态   
0x0012: 0x0000 系统工作模式   
0x0013: 5.6    输入电压     
0x0014: 0.0    电感电流     
0x0015: 11.1   12V电压    
0x0016: 57.2   输出电压     
0x0017: 0.01   输入电流     
0x0018: 20.9   温度1      
0x0019: 22.0   温度2      
0x001A: 0.0    输入功率     
0x001C: 22.0   设备温度     
0x001D: 0x0000 开关机状态    
0x001E: 54.0   电池电压     
0x001F: 700.0  并机功率限值   
0x0021: 56.5   输出限功率电压阈值
Time Stamp: Mon Dec 16 15:44:58 2024
Success Frame: 4
Failed  Frame: 0
Max Series Failed Frame: 0
Parse Result:
0x000C: 0xFFFF 未知数据     
0x000D: 0xFFFF 未知数据     
0x000E: 0x0000 故障字1     
0x000F: 0x0000 故障字2     
0x0010: 0x0000 MPPT工作状态 
0x0011: 0x0000 系统工作状态   
0x0012: 0x0000 系统工作模式   
0x0013: 5.6    输入电压     
0x0014: 0.0    电感电流     
0x0015: 11.1   12V电压    
0x0016: 57.2   输出电压     
0x0017: 0.01   输入电流     
0x0018: 20.9   温度1      
0x0019: 22.0   温度2      
0x001A: 0.0    输入功率     

KeyboardInterrupt: 

# 解除限功率限制
1. 设置输出限功率阈值电压为60V
2. 输出电压停机阈值上升至58.5V
3. 输出电压启机阈值上升至58V

In [8]:
# 解除限功率限制
dev_lamina.frame_write_one(0x21, 600)
time.sleep(0.5)
# 接触输出电压停机限制
dev_lamina.frame_write_one(0x6A, 585)
time.sleep(0.5)
# 修改输出电压启机限制
dev_lamina.frame_write_one(0x68, 580)
time.sleep(0.5)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 21 02 58 D9 5A A8 16
Read Frame:  68 16 95 11 16 06 24 68 9F 08 01 06 00 21 02 58 D9 5A 28 16
Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 6A 02 49 69 40 58 16
Read Frame:  68 16 95 11 16 06 24 68 9F 08 01 06 00 6A 02 49 69 40 D8 16
Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 68 02 44 09 45 F6 16
Read Frame:  68 16 95 11 16 06 24 68 9F 08 01 06 00 68 02 44 09 45 76 16


In [7]:
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Error Info:  No frame data


False

In [104]:
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Read Frame:  68 16 95 11 16 06 24 68 9F 2D 01 03 28 00 00 00 00 00 03 00 03 00 00 01 B1 06 A1 00 6F 02 49 05 D2 01 05 00 D5 D8 32 00 09 01 05 00 01 02 1C AE 60 00 0A 02 58 76 3F EE 16
Parse Result:
0x000E: 0x0000 故障字1     
0x000F: 0x0000 故障字2     
0x0010: 0x0003 MPPT工作状态 
0x0011: 0x0003 系统工作状态   
0x0012: 0x0000 系统工作模式   
0x0013: 43.3   输入电压     
0x0014: 16.97  电感电流     
0x0015: 11.1   12V电压    
0x0016: 58.5   输出电压     
0x0017: 14.9   输入电流     
0x0018: 26.1   温度1      
0x0019: 21.3   温度2      
0x001A: 645.17 输入功率     
0x001C: 26.1   设备温度     
0x001D: 0x0001 开关机状态    
0x001E: 54.0   电池电压     
0x001F: 700.0  并机功率限值   
0x0021: 60.0   输出限功率电压阈值


True

In [156]:
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Read Frame:  68 16 95 11 16 06 24 68 9F 2D 01 03 28 00 00 00 00 00 03 00 03 00 00 01 A7 06 D7 00 6F 02 49 05 FD 01 27 00 E6 E5 0B 00 09 01 27 00 01 02 1C AE 60 00 0A 02 58 4F 90 AA 16
Parse Result:
0x000E: 0x0000  故障字1     
0x000F: 0x0000  故障字2     
0x0010: 0x0003  MPPT工作状态 
0x0011: 0x0003  系统工作状态   
0x0012: 0x0000  系统工作模式   
0x0013: 42.3    输入电压     
0x0014: 17.51   电感电流     
0x0015: 11.1    12V电压    
0x0016: 58.5    输出电压     
0x0017: 15.33   输入电流     
0x0018: 29.5    温度1      
0x0019: 23.0    温度2      
0x001A: 648.459 输入功率     
0x001C: 29.5    设备温度     
0x001D: 0x0001  开关机状态    
0x001E: 54.0    电池电压     
0x001F: 700.0   并机功率限值   
0x0021: 60.0    输出限功率电压阈值


True

In [157]:
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Read Frame:  68 16 95 11 16 06 24 68 9F 2D 01 03 28 00 00 00 00 00 03 00 03 00 00 01 A7 06 D8 00 6F 02 49 05 FD 01 2B 00 E8 E5 0B 00 09 01 2B 00 01 02 1C AE 60 00 0A 02 58 07 E9 C6 16
Parse Result:
0x000E: 0x0000  故障字1     
0x000F: 0x0000  故障字2     
0x0010: 0x0003  MPPT工作状态 
0x0011: 0x0003  系统工作状态   
0x0012: 0x0000  系统工作模式   
0x0013: 42.3    输入电压     
0x0014: 17.52   电感电流     
0x0015: 11.1    12V电压    
0x0016: 58.5    输出电压     
0x0017: 15.33   输入电流     
0x0018: 29.9    温度1      
0x0019: 23.2    温度2      
0x001A: 648.459 输入功率     
0x001C: 29.9    设备温度     
0x001D: 0x0001  开关机状态    
0x001E: 54.0    电池电压     
0x001F: 700.0   并机功率限值   
0x0021: 60.0    输出限功率电压阈值


True

# 运行效果
1. 设备以650W功率正常运行
2. 输出电压采样结果上升至58.5V

In [11]:
dev_lamina.frame_write_one(0x50, 0)
time.sleep(1.5)
dev_lamina.frame_read(0x0E, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 50 00 00 89 DB AE 16
Read Frame:  68 88 88 88 88 89 22 68 9F 08 01 06 00 50 00 00 89 DB FD 16
Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 00 0E 00 20 25 D1 1B 16
Read Frame:  68 88 88 88 88 89 22 68 9F 2D 01 03 28 00 00 00 00 00 01 00 00 00 00 02 0D 00 00 00 72 02 17 00 00 01 1A 01 00 00 00 00 00 01 1A 00 00 02 1C AE 60 00 0A 02 35 06 1D F5 16
Parse Result:
0x000E: 0x0000 故障字1     
0x000F: 0x0000 故障字2     
0x0010: 0x0001 MPPT工作状态 
0x0011: 0x0000 系统工作状态   
0x0012: 0x0000 系统工作模式   
0x0013: 52.5   输入电压     
0x0014: 0.0    电感电流     
0x0015: 11.4   12V电压    
0x0016: 53.5   输出电压     
0x0017: 0.0    输入电流     
0x0018: 28.2   温度1      
0x0019: 25.6   温度2      
0x001A: 0.0    输入功率     
0x001C: 28.2   设备温度     
0x001D: 0x0000 开关机状态    
0x001E: 54.0   电池电压     
0x001F: 700.0  并机功率限值   
0x0021: 56.5   输出限功率电压阈值


True

In [10]:
dev_lamina.frame_read(0x1A0, 0x60)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 01 A0 00 60 44 3C 78 16
Read Frame:  68 88 88 88 88 89 22 68 9F C5 01 03 C0 02 A2 01 00 01 09 14 50 6F 77 65 72 20 66 61 73 74 20 72 65 6C 65 61 73 65 2E 00 00 00 00 00 00 5C 9B 01 00 01 08 0D 53 79 73 20 70 72 65 72 52 75 6E 2E 00 00 00 00 00 00 00 00 00 00 00 00 00 92 9A 01 00 01 07 0D 53 79 73 20 73 74 61 72 74 75 70 2E 00 00 00 00 00 00 00 00 00 00 00 00 00 C0 92 01 00 02 06 08 41 00 00 00 00 0E 02 19 02 00 00 00 00 58 1B 00 00 46 61 75 6C 74 20 52 65 0E 0A 01 00 02 05 08 21 01 00 00 00 5C 02 58 02 00 00 00 00 58 1B 01 00 46 61 75 6C 74 20 54 72 0E 0A 01 00 01 04 0D 53 79 73 20 73 74 61 72 74 75 70 2E 00 00 00 00 00 00 00 00 00 00 00 00 00 D9 6B 77 16
Parse Result:
0x01A0: Event: 1
	time: 107010
	number: 9
	Data: Power fast release.
                                                                                                                                                                                                           事

True

In [24]:
dev_lamina.frame_write_one(0x6F, 2390)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 06 00 6F 09 56 3F B9 C0 16
Read Frame:  68 88 88 88 88 89 22 68 9F 08 01 06 00 6F 09 56 3F B9 0F 16


True

In [11]:
dev_lamina.close_connection()
time.sleep(0.5)
dev_lamina.open_connection()
dev_lamina.frame_read(0x100, 0x20)

Send Frame:  68 AA AA AA AA AA AA 68 1F 08 01 03 01 00 00 20 45 EE 4B 16
Error Info:  No frame data


False

In [8]:
dev_lamina.frame_write_str()

Send Frame:  68 AA AA AA AA AA AA 68 1F 0F 01 10 00 82 00 03 06 05 06 03 04 01 02 09 23 D7 16
Read Frame:  68 01 02 03 04 05 06 68 9F 08 01 10 00 82 00 03 20 20 62 16


True